<a href="https://colab.research.google.com/github/shashankbhagat/Multilabel-Image-Classification/blob/master/Multi_Label_Image_Classification.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
!pip install -U -q PyDrive

In [0]:
from pydrive.auth import GoogleAuth
from pydrive.drive import GoogleDrive
from google.colab import auth
from oauth2client.client import GoogleCredentials
# Authenticate and create the PyDrive client.
auth.authenticate_user()
gauth = GoogleAuth()
gauth.credentials = GoogleCredentials.get_application_default()
drive = GoogleDrive(gauth)

In [66]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [0]:
import keras
from keras.models import Sequential
from keras.layers import Dense, Dropout,Flatten
from keras.layers import Conv2D, MaxPool2D
from keras.utils import to_categorical
from keras.preprocessing import image
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from tqdm import tqdm
import os
import re
import pickle
import multiprocessing as mp
import threading as th
%matplotlib inline

In [0]:
#Download csv from Google Drive
csv_link='https://drive.google.com/open?id=1fHX_qjo6zMZZyLHVLpdxtYnG528tU_U4'
temp, csv_id=csv_link.split('=')
downloaded=drive.CreateFile({'id':csv_id})
downloaded.GetContentFile('train.csv')


In [68]:
train=pd.read_csv('/content/drive/My Drive/Datsets/Multi_label_image_classification/train.csv')
train.head()

Id                                Genre  ...  War  Western
0  tt0086425                  ['Comedy', 'Drama']  ...    0        0
1  tt0085549        ['Drama', 'Romance', 'Music']  ...    0        0
2  tt0086465                           ['Comedy']  ...    0        0
3  tt0086567               ['Sci-Fi', 'Thriller']  ...    0        0
4  tt0086034  ['Action', 'Adventure', 'Thriller']  ...    0        0

[5 rows x 27 columns]

In [69]:
train.columns

Index(['Id', 'Genre', 'Action', 'Adventure', 'Animation', 'Biography',
       'Comedy', 'Crime', 'Documentary', 'Drama', 'Family', 'Fantasy',
       'History', 'Horror', 'Music', 'Musical', 'Mystery', 'N/A', 'News',
       'Reality-TV', 'Romance', 'Sci-Fi', 'Short', 'Sport', 'Thriller', 'War',
       'Western'],
      dtype='object')

In [0]:
#Download images from google drive
pattern=re.compile('[a-zA-Z0-9]+[.]jpg')
local_img_path=os.path.expanduser(os.getcwd()+'/Images')
try:
    os.makedirs(local_img_path)
except: pass

print(local_img_path)
img_folder_link='https://drive.google.com/open?id=1zoWXcDzfjxeYbvOknbGU5WyM707yDGcP'
temp,img_folder_id=img_folder_link.split('=')
print(img_folder_id)
#downloaded=drive.CreateFile({'id':img_folder_id})
#downloaded.GetContentFile('Images')
fileList=drive.ListFile({'q':"'{}' in parents".format(str(img_folder_id))}).GetList()
for f in tqdm(fileList):
    #print(f['title'])
    if bool(re.match(pattern,f['title'])):
        try:
            fname=os.path.join(local_img_path,f['title'])
            downloaded=drive.CreateFile({'id':f['id']})
            downloaded.GetContentFile(fname)
        except: pass

/content/Images
1zoWXcDzfjxeYbvOknbGU5WyM707yDGcP


100%|██████████| 7876/7876 [1:00:24<00:00,  2.37it/s]


Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/drive


In [0]:
import re
pattern=re.compile('[a-zA-Z0-9]+[.]jpg')
print(bool(re.match(pattern,'23sdf3dsfds45.jpg')))

True


In [0]:
train_image=[]
def load_data(start,end):
    print('in load data:',start,end)
    #i=i[0]
    temp=[]
    for i in range(start,end+1):
        img=image.load_img('/content/drive/My Drive/Datsets/Multi_label_image_classification/Images/'+train['Id'][i]+'.jpg',target_size=(400,400,3))
        img=image.img_to_array(img)
        img=img/255
        temp.append(img)
    train_image.append(temp)
    

In [106]:
#preprocessing the data
X=[]
try:
    with open('/content/drive/My Drive/Datsets/Multi_label_image_classification/trainX.bkp',rb) as f:
        X=pickle.load(f)
except: pass
pool=mp.Pool(4)
print('X:',X)
args_list=[]
threads_list=[]
if len(X)==0:
    start=0
    end= -1   #train.shape[0]//4
    a=[]
    for i in range(4):   #cpu_count
        start=end+1    
        end=start+(train.shape[0]//4)
        if i==3:
            end=train.shape[0]
        temp_arg=[start,end]
        args_list.append(temp_arg)

    for val in args_list:        
        print(val)        
        th_temp=th.Thread(target=load_data,args=(val[0],val[1]),)
        threads_list.append(th_temp)
        
    for th in threads_list:
        th.start()

    for th in threads:
        th.join()
    
    #train_image=pool.map(load_data,(val for val in args_list))

    #pool.close()
    #pool.join()
    #train_image=[r.get() for r in result_objects]
    print('done parallel...')

X: []
[0, 1813]
[1814, 3627]
[3628, 5441]
[5442, 7254]
in load data: 0 1813
in load data: in load data: 3628 5441
1814in load data:done parallel...
 3627
 5442 7254


In [107]:

train_image.shape
#X=np.array(train_image)

[[array([[[0.00392157, 0.00392157, 0.00392157],
          [0.00392157, 0.00392157, 0.00392157],
          [0.00392157, 0.00392157, 0.00392157],
          ...,
          [0.00392157, 0.00392157, 0.00392157],
          [0.00392157, 0.00392157, 0.00392157],
          [0.00784314, 0.00784314, 0.        ]],
  
         [[0.00392157, 0.00392157, 0.00392157],
          [0.00392157, 0.00392157, 0.00392157],
          [0.00392157, 0.00392157, 0.00392157],
          ...,
          [0.00392157, 0.00392157, 0.00392157],
          [0.00392157, 0.00392157, 0.00392157],
          [0.00784314, 0.00784314, 0.        ]],
  
         [[0.00392157, 0.00392157, 0.00392157],
          [0.00392157, 0.00392157, 0.00392157],
          [0.00392157, 0.00392157, 0.00392157],
          ...,
          [0.00392157, 0.00392157, 0.00392157],
          [0.00392157, 0.00392157, 0.00392157],
          [0.00784314, 0.00784314, 0.        ]],
  
         ...,
  
         [[0.11372549, 0.11372549, 0.11372549],
          [0.0

In [0]:
with open('/content/drive/My Drive/Datsets/Multi_label_image_classification/trainX.bkp',wb) as f:
    pickle.dump(X,f)

In [0]:
a=0
print(train.shape[0])
for i in range(train.shape[0]):
    print([i])
    a=[i]


In [0]:
start=0
end=-1 #train.shape[0]//4
a=[]
for i in range(4):
    start=end+1    
    end=start+(train.shape[0]//4)
    if i==3:
        end=train.shape[0]
    a.append([start,end])
print(a)

[[0, 1813], [1814, 3627], [3628, 5441], [5442, 7254]]


In [0]:
train.shape[0]

7254

Process ForkPoolWorker-165:
Process ForkPoolWorker-167:
Process ForkPoolWorker-164:
Process ForkPoolWorker-166:
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
  File "/usr/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()


KeyboardInterrupt: ignored

Traceback (most recent call last):
  File "/usr/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/usr/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/usr/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
